> NOTE: Forecast-lead stacking build (2024-01-08)

# Google Colab: Tropical Cyclone Tracking & Environment Extraction

This notebook mirrors the project's cyclone tracking + environment extraction algorithms inside a Colab runtime. It follows the steps described in `Colab_Implementation_Guide.md` and is tuned for the default Colab kernel (12 GB RAM / 100 GB disk).

## Notebook Roadmap

- Inspect runtime limits and bootstrap the repository
- Install dependencies required by the tracker and extractor modules
- Stream WeatherBench 2 HRES data (`gs://weatherbench2/datasets/hres_t0/...`) via Zarr + xarray/gcsfs
- Run the cyclone tracker directly against the in-memory Dataset
- Slice the Dataset around individual tracks and feed it to `TCEnvironmentalSystemsExtractor`
- Persist outputs to `colab_outputs/` inside the repo

In [1]:
!nvidia-smi || true
!free -h
!df -h /content

/bin/bash: line 1: nvidia-smi: command not found
               total        used        free      shared  buff/cache   available
Mem:            12Gi       607Mi       8.9Gi       1.0Mi       3.2Gi        11Gi
Swap:             0B          0B          0B
Filesystem      Size  Used Avail Use% Mounted on
overlay         226G   39G  188G  17% /


In [4]:
# 强制使用“无浏览器”模式进行认证
# 这会在输出栏打印一个长链接，让你复制到普通浏览器中打开
!gcloud auth application-default login --no-launch-browser


The environment variable [GOOGLE_APPLICATION_CREDENTIALS] is set to:
  [/content/.adc/adc.json]
Credentials will still be generated to the default location:
  [/content/.config/application_default_credentials.json]
To use these credentials, unset this environment variable before
running your application.

Do you want to continue (Y/n)?  

Command killed by keyboard interrupt

^C


In [2]:
import os
import getpass
print(f"User: {getpass.getuser()}")
print(f"UID: {os.getuid()}")
print(f"CWD: {os.getcwd()}")
print(f"List /content/TianGong-AI-Cyclone: {os.listdir('/content/TianGong-AI-Cyclone') if os.path.exists('/content/TianGong-AI-Cyclone') else 'Not Found'}")

User: root
UID: 0
CWD: /content
List /content/TianGong-AI-Cyclone: Not Found


In [3]:
import os
from pathlib import Path

CANDIDATE_ROOTS = [
    Path.cwd().resolve(),
    Path("/content/TianGong-AI-Cyclone"),
]

output_dir = None
for root in CANDIDATE_ROOTS:
    candidate = root / "colab_outputs"
    if candidate.exists():
        output_dir = candidate
        break

if output_dir is None:
    output_dir = CANDIDATE_ROOTS[0] / "colab_outputs"

tracks_dir = output_dir / "tracks"
json_dir = output_dir / "analysis_json"

print(f"Inspecting outputs under: {output_dir}")

if not output_dir.exists():
    print("Output directory not found yet. It will be created after the bootstrap step.")
else:
    if tracks_dir.exists():
        track_count = len(list(tracks_dir.glob("*.csv")))
        print(f"Found {track_count} track files.")
    else:
        print("Tracks directory not found.")

    if json_dir.exists():
        json_count = len(list(json_dir.glob("*.json")))
        print(f"Found {json_count} JSON analysis files.")
    else:
        print("JSON directory not found.")


Tracks directory not found.
JSON directory not found.


## 项目初始化 & 环境配置

**适用于 Google Colab 和 HPC 云服务器环境**

两种环境都是云端运行。
假设你已经在云端**手动克隆**了仓库，并且当前工作目录就在项目根目录（包含 `src/`）。
本 Notebook 只需要：
1. 设置项目路径（直接使用当前目录）
2. 安装依赖
3. 设置输出目录（写入项目目录内）
4. 配置 Python 路径

已取消 Google Drive/rclone 数据同步：所有输出直接写入项目内的 `colab_outputs/`。

In [4]:
import os
import sys
from pathlib import Path

# ============================================================================
# 环境检测
# ============================================================================
def is_colab():
    """检测是否在 Google Colab 环境中运行"""
    try:
        import google.colab  # type: ignore
        return True
    except Exception:
        return False

RUNNING_ON_COLAB = is_colab()

print(f"🖥️ 运行环境检测:")
print(f"   - Google Colab: {RUNNING_ON_COLAB}")

# ============================================================================
# 配置路径 - 假设仓库已手动克隆，且当前目录位于仓库内
# ============================================================================
def find_project_root(start: Path) -> Path:
    """从当前目录向上查找项目根目录（包含 src/）。"""
    for candidate in [start, *start.parents]:
        if (candidate / "src").is_dir():
            return candidate
    return start

PROJECT_PATH = find_project_root(Path.cwd().resolve())

if not (PROJECT_PATH / "src").is_dir():
    raise RuntimeError(
        f"未找到项目根目录：当前目录={Path.cwd().resolve()}。请在仓库根目录（包含 src/）运行该 Notebook。"
    )

# ============================================================================
# 设置输出目录和 Python 路径
# ============================================================================
OUTPUT_ROOT = PROJECT_PATH / "colab_outputs"
OUTPUT_ROOT.mkdir(parents=True, exist_ok=True)

# 确保 src 目录在 Python 路径中
src_path = str(PROJECT_PATH / "src")
if src_path not in sys.path:
    sys.path.insert(0, src_path)

print(f"\n📊 环境配置完成:")
print(f"   - 项目路径: {PROJECT_PATH}")
print(f"   - 输出目录: {OUTPUT_ROOT}")
print(f"   - Python 路径已更新")
print("   - 已跳过 git clone（仓库已手动克隆）")

Cloning repository to /content/TianGong-AI-Cyclone ...
Python path updated.


## Google Drive 同步设置 (已取消)

本版本已取消 Google Drive/rclone 数据同步：所有输出直接写入项目内的 `colab_outputs/`。

In [ ]:
import subprocess
import shutil
from pathlib import Path
from typing import Optional
import os

# ============================================================================
# rclone 同步工具类（已弃用，保留参考；当前不再同步）
# ============================================================================
class GoogleDriveSyncer:
    """（已弃用）Google Drive 同步器 - 支持 HPC 和 Colab 环境"""
    
    def __init__(self, local_path: Path, remote_name: str = "gdrive", remote_path: str = "TianGong-AI-Cyclone/colab_outputs"):
        self.local_path = Path(local_path)
        self.remote_name = remote_name
        self.remote_path = remote_path
        self.rclone_available = self._check_rclone()
        self.is_colab = RUNNING_ON_COLAB
        
    def _check_rclone(self) -> bool:
        """检查 rclone 是否可用"""
        return shutil.which("rclone") is not None
    
    def _install_rclone(self) -> bool:
        """尝试安装 rclone (适用于有写入权限的环境)"""
        print("📦 尝试安装 rclone...")
        try:
            # 在用户目录下安装
            install_dir = Path.home() / ".local" / "bin"
            install_dir.mkdir(parents=True, exist_ok=True)
            
            # 下载并解压 rclone
            subprocess.run([
                "curl", "-O", "https://downloads.rclone.org/rclone-current-linux-amd64.zip"
            ], check=True, capture_output=True)
            subprocess.run(["unzip", "-o", "rclone-current-linux-amd64.zip"], check=True, capture_output=True)
            
            # 找到解压后的目录并复制到用户 bin
            rclone_dirs = list(Path(".").glob("rclone-*-linux-amd64"))
            if rclone_dirs:
                rclone_src = rclone_dirs[0] / "rclone"
                rclone_dst = install_dir / "rclone"
                shutil.copy2(rclone_src, rclone_dst)
                rclone_dst.chmod(0o755)
                
                # 添加到 PATH
                os.environ["PATH"] = f"{install_dir}:{os.environ.get('PATH', '')}"
                self.rclone_available = True
                print(f"✅ rclone 安装成功: {rclone_dst}")
                
                # 清理下载文件
                subprocess.run(["rm", "-rf", "rclone-current-linux-amd64.zip"] + [str(d) for d in rclone_dirs], capture_output=True)
                return True
        except Exception as e:
            print(f"❌ rclone 安装失败: {e}")
        return False
    
    def configure_rclone_headless(self) -> None:
        """配置 rclone - 无浏览器模式 (适用于 HPC 云服务器)"""
        if not self.rclone_available:
            if not self._install_rclone():
                print("❌ 无法安装 rclone，请联系系统管理员")
                return
        
        print("\n" + "="*70)
        print("🔧 rclone Google Drive 配置向导 (HPC 云服务器无浏览器模式)")
        print("="*70)
        print("""
由于 HPC 云服务器没有浏览器，请按以下步骤配置:

【步骤 1】在你的本地电脑上 (有浏览器的机器):
   1. 下载 rclone: https://rclone.org/downloads/
   2. 运行命令: rclone authorize "drive"
   3. 浏览器会打开 Google 授权页面，完成授权
   4. 复制终端显示的 token (一大段 JSON 格式的文本)

【步骤 2】在 HPC 云服务器上运行:
   rclone config

【步骤 3】按提示操作:
   - 输入 n (新建)
   - 输入名称: gdrive
   - 选择: Google Drive (通常是 17 或 drive)
   - client_id: 直接回车 (使用默认)
   - client_secret: 直接回车 (使用默认)
   - scope: 选择 1 (完全访问)
   - service_account_file: 直接回车
   - Edit advanced config: n
   - Use auto config: n (重要！选 n)
   - 粘贴步骤 1 获得的 token
   - Configure as team drive: n
   - 确认: y

【步骤 4】测试连接:
   rclone lsd gdrive:

配置完成后，重新运行此 cell 即可开始同步。
""")
        
    def sync_to_drive(self, verbose: bool = True) -> bool:
        """同步本地目录到 Google Drive"""
        if self.is_colab:
            print("📁 Colab 环境: 数据已直接保存到 Drive，无需额外同步")
            return True
            
        if not self.rclone_available:
            print("⚠️ rclone 不可用，跳过同步。")
            print("   请运行: GDRIVE_SYNCER.configure_rclone_headless()")
            return False
        
        # 检查 rclone 配置是否存在
        config_check = subprocess.run(["rclone", "listremotes"], capture_output=True, text=True)
        if self.remote_name + ":" not in config_check.stdout:
            print(f"⚠️ rclone 远程 '{self.remote_name}' 未配置")
            print("   请运行: GDRIVE_SYNCER.configure_rclone_headless()")
            return False
        
        remote_dest = f"{self.remote_name}:{self.remote_path}"
        
        cmd = [
            "rclone", "sync",
            str(self.local_path),
            remote_dest,
            "--progress" if verbose else "--quiet",
            "--transfers", "4",
            "--checkers", "8",
        ]
        
        if verbose:
            print(f"🔄 同步中: {self.local_path} -> {remote_dest}")
        
        try:
            result = subprocess.run(cmd, capture_output=not verbose, text=True)
            if result.returncode == 0:
                print(f"✅ 同步完成!")
                return True
            else:
                print(f"❌ 同步失败: {result.stderr if result.stderr else 'Unknown error'}")
                return False
        except Exception as e:
            print(f"❌ 同步异常: {e}")
            return False
    
    def sync_single_file(self, file_path: Path) -> bool:
        """同步单个文件到 Google Drive"""
        if self.is_colab:
            return True
            
        if not self.rclone_available:
            return False
        
        try:
            rel_path = file_path.relative_to(self.local_path)
            remote_dest = f"{self.remote_name}:{self.remote_path}/{rel_path}"
            
            subprocess.run([
                "rclone", "copyto",
                str(file_path),
                remote_dest,
                "--quiet"
            ], check=True, capture_output=True)
            return True
        except:
            return False

# ============================================================================
# Google Drive 同步 (已取消)
# ============================================================================
GDRIVE_SYNCER = None
print(f"✅ 已取消 Google Drive/rclone 同步；输出目录: {OUTPUT_ROOT}")

## Install Dependencies

Install the scientific stack required by the tracker and extractor. Re-run this cell whenever you change `requirements.txt`.

In [5]:
import subprocess
import sys

print("Installing project requirements ...")
subprocess.run([sys.executable, "-m", "pip", "install", "-q", "-r", f"{PROJECT_PATH}/requirements.txt"], check=True)
print("Installing Colab-specific extras ...")
subprocess.run([sys.executable, "-m", "pip", "install", "-q", "xarray[complete]", "zarr", "gcsfs", "google-cloud-storage", "tqdm"], check=True)

Installing project requirements ...
Installing Colab-specific extras ...


CompletedProcess(args=['/usr/bin/python3', '-m', 'pip', 'install', '-q', 'xarray[complete]', 'zarr', 'gcsfs', 'google-cloud-storage', 'tqdm'], returncode=0)

## Validate Repository Modules

Ensure the notebook imports the tracker/extractor implementations directly from the cloned repository. This avoids mismatches with older versions that may already be installed in the Colab VM.


In [ ]:
import importlib
from pathlib import Path

assert 'PROJECT_PATH' in globals(), "Run the bootstrap cell first so PROJECT_PATH is defined."
SRC_ROOT = (PROJECT_PATH / 'src').resolve()
MODULES_TO_CHECK = {
    'initial_tracker': 'Cyclone tracker',
    'environment_extractor': 'Environment extractor',
}

for module_name, label in MODULES_TO_CHECK.items():
    module = importlib.import_module(module_name)
    module_path = Path(module.__file__).resolve()
    if SRC_ROOT not in module_path.parents:
        raise RuntimeError(
            f"{label} ({module_name}) was imported from {module_path}, not from {SRC_ROOT}."
            "\nPlease verify that PROJECT_PATH points to the repo you just cloned."
        )
    print(f"{label} -> {module_path}")


In [6]:
import xarray as xr
import pandas as pd
import numpy as np

# ============================================================================
# 1. WeatherBench 2 HRES 预报数据集配置
# ============================================================================

# 💡 WeatherBench 2 HRES 数据集 (2016-2022, 公开访问)
# 文档: https://weatherbench2.readthedocs.io/
DATASET_URL = "gs://weatherbench2/datasets/hres/2016-2022-0012-1440x721.zarr"
STORAGE_OPTIONS = {"token": "anon"}  # 匿名访问，无需认证

print(f"📡 数据集 URL: {DATASET_URL}")
print(f"🔓 访问模式: 匿名公开访问 (无需 Google Cloud 认证)")

# ============================================================================
# 2. 验证数据集可访问性
# ============================================================================

print(f"\n正在连接数据集...")
try:
    ds_check = xr.open_zarr(DATASET_URL, storage_options=STORAGE_OPTIONS, consolidated=True)
    print("✅ 数据集连接成功!")
    
    # 打印维度信息
    print("\n" + "="*50)
    print(" 数据集维度结构")
    print("="*50)
    for dim, size in ds_check.sizes.items():
        print(f"  - {dim}: {size}")
    
    # 打印可用变量
    print("\n" + "="*50)
    print(" 可用变量")
    print("="*50)
    for var in list(ds_check.data_vars)[:15]:
        print(f"  - {var}")
    if len(ds_check.data_vars) > 15:
        print(f"  ... 共 {len(ds_check.data_vars)} 个变量")
    
    # 时间范围
    if "time" in ds_check.coords:
        time_min = pd.Timestamp(ds_check["time"].values.min())
        time_max = pd.Timestamp(ds_check["time"].values.max())
        print(f"\n📅 时间范围: {time_min.strftime('%Y-%m-%d')} 至 {time_max.strftime('%Y-%m-%d')}")
    
    # 内存估算
    print("\n" + "="*50)
    print(" 内存占用估算")
    print("="*50)
    if "time" in ds_check.dims:
        one_forecast = ds_check.isel(time=0)
        total_gb = one_forecast.nbytes / 1e9
        print(f"  单个起报时间完整数据: {total_gb:.2f} GB")
        
        if 'prediction_timedelta' in ds_check.coords:
            steps = ds_check.sizes.get('prediction_timedelta', 1)
            single_step_gb = total_gb / steps if steps > 0 else total_gb
            print(f"  单个预报步长 (6h): ~{single_step_gb:.2f} GB")
            print(f"\n💡 提示: 多进程处理时每个进程独立加载数据，")
            print(f"        建议 MAX_WORKERS × 单步内存 < 可用内存的 80%")
    
    ds_check.close()
    
except Exception as e:
    print(f"❌ 数据集连接失败: {e}")
    print("\n可能的原因:")
    print("  1. 网络连接问题 - 检查是否能访问 Google Cloud Storage")
    print("  2. 防火墙限制 - HPC 可能需要代理设置")
    print("  3. gcsfs 未安装 - 运行: pip install gcsfs")
    
    print("\n💡 测试网络连接:")
    print("  curl -I https://storage.googleapis.com/weatherbench2/")
    
    raise

正在检查数据集元数据: gs://weatherbench2/datasets/hres/2016-2022-0012-1440x721.zarr ...


/tmp/ipython-input-3611659504.py:10: FutureWarning: In a future version, xarray will not decode the variable 'prediction_timedelta' into a timedelta64 dtype based on the presence of a timedelta-like 'units' attribute by default. Instead it will rely on the presence of a timedelta64 'dtype' attribute, which is now xarray's default way of encoding timedelta64 values.
To continue decoding into a timedelta64 dtype, either set `decode_timedelta=True` when opening this dataset, or add the attribute `dtype='timedelta64[ns]'` to this variable on disk.
To opt-in to future behavior, set `decode_timedelta=False`.
  ds_check = xr.open_zarr(DATASET_URL, storage_options=STORAGE_OPTIONS, consolidated=True)



 维度结构检查 (Dimensions) 
- time: 5134
- prediction_timedelta: 41
- latitude: 721
- longitude: 1440
- level: 13

 内存爆炸计算器 (Memory Crash Investigator) 
【结论】：加载单个起报时间 (time=0) 的完整数据需要：
👉 17.03 GB 👈

🚨 警告：这已经超过了 Colab 的 12GB RAM 上限！
如果不切除 'prediction_timedelta' 维度，试图加载哪怕一个气旋的数据都可能导致 OOM。

【对比】：如果只取第 0 小时 (prediction_timedelta=0)：
👉 仅需 0.42 GB
(这就是为什么不加 slice 就会导致内存暴增 41 倍)

 隐形杀手：Zarr 分块 (Chunk Sizes) 
变量 'temperature' 的分块策略: ((1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1

## Configure WeatherBench 2 Dataset

Tune the parameters below to keep the spatial/temporal subset within the 12 GB budget. Longitudes in the IFS HRES archive live in `[0, 360)`, so wrap western values via `lon % 360`.

**Time Range Options** (HRES has full 2016-2022 data available):
- **12 days** (current): `("2020-07-25", "2020-08-05")` → 48 timesteps, ~150 MB (demo)
- **1 month**: `("2020-08-01", "2020-08-31")` → ~120 timesteps, ~400 MB
- **3 months**: `("2020-07-01", "2020-09-30")` → ~365 timesteps, ~1.2 GB
- **6 months**: `("2020-01-01", "2020-06-30")` → ~730 timesteps, ~2.4 GB
- **1 year**: `("2020-01-01", "2020-12-31")` → ~1460 timesteps, ~4.8 GB
- **Multi-year**: `("2018-01-01", "2020-12-31")` → only with aggressive spatial filtering

Adjust `LAT_RANGE` and `LON_RANGE` to reduce memory if needed.

In [7]:
import numpy as np
import pandas as pd
import xarray as xr
from pathlib import Path

# ✅ SWITCH TO FORECAST DATA
DATASET_URL = "gs://weatherbench2/datasets/hres/2016-2022-0012-1440x721.zarr"
TRACKS_CSV = PROJECT_PATH / "input" / "matched_cyclone_tracks.csv"

# ============================================================================
# 1. Load & Filter Tracks (2016-2022)
# ============================================================================
print(f"Loading tracks from: {TRACKS_CSV}")
df_tracks = pd.read_csv(TRACKS_CSV)
df_tracks["dt"] = pd.to_datetime(df_tracks["datetime"])

# Filter for HRES range (2016-2022)
HRES_START = pd.Timestamp("2016-01-01")
HRES_END = pd.Timestamp("2022-12-31")
mask = (df_tracks["dt"] >= HRES_START) & (df_tracks["dt"] <= HRES_END)
valid_storm_ids = df_tracks[mask]["storm_id"].unique()

print(f"✅ Found {len(valid_storm_ids)} storms within HRES dataset range (2016-2022).")
print(f"   Example IDs: {valid_storm_ids[:5]}")

# ============================================================================
# 2. Prepare Global Dataset Adapter (Lazy Loading)
# ============================================================================
CHUNKS = {"time": 1, "latitude": 181, "longitude": 361}
STORAGE_OPTIONS = {"token": "anon"}
CONSOLIDATED_METADATA = True

rename_map = {
    "mean_sea_level_pressure": "msl",
    "10m_u_component_of_wind": "u10",
    "10m_v_component_of_wind": "v10",
    "u_component_of_wind": "u",        # ✅ Multi-level wind
    "v_component_of_wind": "v",        # ✅ Multi-level wind
    "temperature": "t",                # Temperature
    "specific_humidity": "q",          # Humidity
    "geopotential": "z",
    "land_sea_mask": "lsm",
    "2m_temperature": "t2m",           # SST proxy
}

print("\nOpening WeatherBench 2 FORECAST dataset (Lazy)...")
ds_raw = xr.open_zarr(
    DATASET_URL,
    consolidated=CONSOLIDATED_METADATA,
    storage_options=STORAGE_OPTIONS,
)

present = {src: dst for src, dst in rename_map.items() if src in ds_raw}
ds_adapted = ds_raw[list(present.keys())].rename(present)

if "z" in ds_adapted:
    ds_adapted["z"] = ds_adapted["z"] / 9.80665

# Synthetic LSM if missing
if "lsm" not in ds_adapted:
    lat_dim = "latitude" if "latitude" in ds_adapted.coords else "lat"
    lon_dim = "longitude" if "longitude" in ds_adapted.coords else "lon"
    n_lat = len(ds_adapted[lat_dim])
    n_lon = len(ds_adapted[lon_dim])
    ds_adapted["lsm"] = xr.DataArray(
        np.zeros((n_lat, n_lon), dtype=np.float32),
        coords={lat_dim: ds_adapted[lat_dim], lon_dim: ds_adapted[lon_dim]},
        dims=[lat_dim, lon_dim],
        name="lsm"
    )

# Note: Forecast data typically has (time, prediction_timedelta, lat, lon)
# We do NOT chunk prediction_timedelta heavily as we need the full sequence for tracking
ds_adapted = ds_adapted.chunk(CHUNKS)
print("✅ Dataset adapter ready.")

# ============================================================================
# 3. Helper to get context for a specific storm (Forecast Version)
# ============================================================================
def get_storm_context(storm_id):
    storm_data = df_tracks[df_tracks["storm_id"] == storm_id]
    if storm_data.empty:
        raise ValueError(f"Storm {storm_id} not found")
    
    # Dynamic Range
    pad_days = 1
    pad_deg = 10.0
    
    start_dt = storm_data["dt"].min() - pd.Timedelta(days=pad_days)
    end_dt = storm_data["dt"].max() + pd.Timedelta(days=pad_days)
    
    # Longitude handling
    lons = storm_data["longitude"].values
    lons_360 = np.where(lons < 0, lons + 360, lons)
    lon_min = max(0, lons_360.min() - pad_deg)
    lon_max = min(360, lons_360.max() + pad_deg)
    
    lat_min = max(-90, storm_data["latitude"].min() - pad_deg)
    lat_max = min(90, storm_data["latitude"].max() + pad_deg)
    
    # Slicing
    LAT_NAME = "latitude" if "latitude" in ds_adapted.coords else "lat"
    LON_NAME = "longitude" if "longitude" in ds_adapted.coords else "lon"
    
    # Helper slices
    def _lat_slice(coord, bounds):
        lower, upper = bounds
        if coord[0] > coord[-1]: lower, upper = upper, lower
        return slice(lower, upper)

    def _lon_slice(coord, bounds):
        lower, upper = bounds
        coord_min, coord_max = float(coord.min()), float(coord.max())
        if coord_min >= 0:
            lower = lower % 360
            upper = upper % 360
        if lower > upper:
             raise ValueError(f"Longitude selection crosses dateline for {storm_id}. Manual handling required.")
        lower = max(lower, coord_min)
        upper = min(upper, coord_max)
        return slice(lower, upper)

    lat_s = _lat_slice(ds_adapted[LAT_NAME].values, (lat_min, lat_max))
    lon_s = _lon_slice(ds_adapted[LON_NAME].values, (lon_min, lon_max))
    
    # For forecast data, 'time' is the initialization time.
    # We select all initializations within the storm's lifespan.
    ds_focus = ds_adapted.sel({
        LAT_NAME: lat_s, 
        LON_NAME: lon_s, 
        "time": slice(start_dt.strftime("%Y-%m-%d"), end_dt.strftime("%Y-%m-%d"))
    })
    
    return ds_focus, storm_data["dt"].min().strftime("%Y-%m-%d %H:%M")

Loading tracks from: /content/TianGong-AI-Cyclone/input/matched_cyclone_tracks.csv
✅ Found 256 storms within HRES dataset range (2016-2022).
   Example IDs: ['2016007N27285' '2016040S16155' '2016148N27288' '2016158N22272'
 '2016171N19268']

Opening WeatherBench 2 FORECAST dataset (Lazy)...


/tmp/ipython-input-3186991231.py:47: FutureWarning: In a future version, xarray will not decode the variable 'prediction_timedelta' into a timedelta64 dtype based on the presence of a timedelta-like 'units' attribute by default. Instead it will rely on the presence of a timedelta64 'dtype' attribute, which is now xarray's default way of encoding timedelta64 values.
To continue decoding into a timedelta64 dtype, either set `decode_timedelta=True` when opening this dataset, or add the attribute `dtype='timedelta64[ns]'` to this variable on disk.
To opt-in to future behavior, set `decode_timedelta=False`.
  ds_raw = xr.open_zarr(


: 

: 

: 

## Cyclone Tracking Helpers

The function below adapts the existing tracker to run directly on the Zarr-backed Dataset without writing intermediate NetCDF files.

In [10]:
from pathlib import Path
from typing import Dict

import pandas as pd
import numpy as np
import xarray as xr

from initial_tracker.dataset_adapter import _DsAdapter, _build_batch_from_ds_fast
from initial_tracker.initials import _load_all_points, _select_initials_for_time
from initial_tracker.tracker import Tracker
from initial_tracker.exceptions import NoEyeException

def _normalize_lon_for_grid(lon_value: float, lon_grid: np.ndarray) -> float:
    lon = float(lon_value)
    grid_min = float(lon_grid.min())
    grid_max = float(lon_grid.max())
    if grid_min >= 0 and lon < 0:
        lon = lon % 360
    if grid_max <= 180 and lon > 180:
        lon = ((lon + 180) % 360) - 180
    return lon

def track_cyclones_from_dataset(
    ds: xr.Dataset,
    initials_csv: str | Path,
    *,
    target_storm_id: str | None = None,
    start_time: str | pd.Timestamp | None = None,
    time_window_hours: int = 6,
    max_storms: int | None = 3,
    max_steps: int | None = 40,
    output_dir: str | Path | None = None,
) -> dict[str, pd.DataFrame]:
    adapter = _DsAdapter.build(ds)
    times = pd.Index(adapter.times)
    if len(times) == 0:
        raise ValueError("Dataset has no time dimension.")

    if start_time is None:
        start_idx = 0
    else:
        start_time = pd.Timestamp(start_time)
        start_idx = int(np.argmin(np.abs(times - start_time)))

    all_initials = _load_all_points(Path(initials_csv))
    if all_initials.empty:
        raise ValueError("Initials CSV produced an empty DataFrame.")
    init_candidates = _select_initials_for_time(all_initials, times[start_idx], tol_hours=time_window_hours)
    
    if target_storm_id is not None:
        init_candidates = init_candidates[init_candidates["storm_id"] == target_storm_id]
        if init_candidates.empty:
             print(f"Warning: Target storm {target_storm_id} not found in candidates at {times[start_idx]}.")
             return {}

    if init_candidates.empty:
        raise RuntimeError("No storms matched the requested time window.")

    output_path = Path(output_dir) if output_dir else None
    if output_path:
        output_path.mkdir(parents=True, exist_ok=True)

    time_lookup = {pd.Timestamp(t): idx for idx, t in enumerate(adapter.times)}
    tracks: dict[str, pd.DataFrame] = {}
    processed = 0

    for _, row in init_candidates.sort_values("storm_id").iterrows():
        if max_storms is not None and processed >= max_storms:
            break

        storm_id = str(row["storm_id"])
        init_lat = float(row["init_lat"])
        init_lon = _normalize_lon_for_grid(float(row["init_lon"]), adapter.lons)
        init_wind = float(row["max_wind_usa"]) if pd.notna(row.get("max_wind_usa")) else None
        init_msl = float(row["min_pressure_usa"]) * 100.0 if pd.notna(row.get("min_pressure_usa")) else None

        tracker = Tracker(
            init_lat=init_lat,
            init_lon=init_lon,
            init_time=times[start_idx],
            init_msl=init_msl,
            init_wind=init_wind,
        )

        last_idx = len(adapter.times) if max_steps is None else min(len(adapter.times), start_idx + max_steps)
        for time_idx in range(start_idx, last_idx):
            batch = _build_batch_from_ds_fast(adapter, time_idx)
            try:
                tracker.step(batch)
            except NoEyeException as exc:
                if time_idx == start_idx:
                    print(f"[{storm_id}] Failed on the first step: {exc}")
                    tracker = None
                    break
                print(f"[{storm_id}] Warning: skipping time {adapter.times[time_idx]} -> {exc}")
                continue
            if tracker.dissipated:
                break

        if tracker is None:
            continue

        df = tracker.results()
        df["storm_id"] = storm_id
        df["particle"] = storm_id
        df["time_idx"] = df["time"].map(time_lookup).astype("Int64")
        tracks[storm_id] = df

        if output_path:
            out_csv = output_path / f"track_{storm_id}_colab.csv"
            df.to_csv(out_csv, index=False)
            print(f"[{storm_id}] track saved to {out_csv}")

        processed += 1

    return tracks

### Run the Tracker

Keep `max_storms` / `max_steps` small for interactive use; expand them once you are satisfied with the configuration.

In [ ]:
from IPython.display import display
import os
import shutil
import gc
import multiprocessing as mp
from multiprocessing import Pool, Manager
from functools import partial
import time
from environment_extractor.extractor import TCEnvironmentalSystemsExtractor

# ============================================================================
# 4. Define Environment Extraction Helpers
# ============================================================================

def prepare_single_forecast_dataset(ds_single: xr.Dataset) -> xr.Dataset:
    """
    Converts a single forecast initialization (with prediction_timedelta) 
    into a valid-time series dataset for the tracker.
    Enforces 6-hourly steps.
    """
    if "time" in ds_single.coords:
        ds = ds_single.rename({"time": "init_time"})
    else:
        ds = ds_single
        
    if "prediction_timedelta" not in ds.coords:
        if "init_time" in ds.coords:
            return ds.rename({"init_time": "time"})
        return ds

    pt = ds["prediction_timedelta"]
    hours = (pt.values.astype("timedelta64[ns]").astype(float) / (3600 * 1e9))
    keep_mask = (np.abs(hours % 6) < 0.01)
    ds = ds.isel(prediction_timedelta=keep_mask)

    init_ts = pd.Timestamp(ds["init_time"].values)
    lead_offsets = ds["prediction_timedelta"].values
    
    if not np.issubdtype(lead_offsets.dtype, np.timedelta64):
        lead_offsets = pd.to_timedelta(lead_offsets)
        
    valid_times = init_ts + lead_offsets
    
    ds = ds.assign_coords(valid_time=("prediction_timedelta", valid_times))
    ds = ds.swap_dims({"prediction_timedelta": "valid_time"})
    ds = ds.rename({"valid_time": "time"})
    
    return ds

def subset_dataset_for_track(
    ds: xr.Dataset,
    track_df: pd.DataFrame,
    lat_pad: float = 8.0,
    lon_pad: float = 8.0,
    time_pad_steps: int = 2,
) -> xr.Dataset:
    if track_df.empty:
        raise ValueError("Track DataFrame is empty.")
    
    LAT_NAME = "latitude" if "latitude" in ds.coords else "lat"
    LON_NAME = "longitude" if "longitude" in ds.coords else "lon"

    lat_vals = track_df["lat"].astype(float)
    lon_vals = track_df["lon"].astype(float)
    lon_grid = ds[LON_NAME].values
    lon_is_0360 = float(lon_grid.min()) >= 0
    
    if lon_is_0360:
        lon_vals = lon_vals % 360
        
    lat_min = max(lat_vals.min() - lat_pad, float(ds[LAT_NAME].values.min()))
    lat_max = min(lat_vals.max() + lat_pad, float(ds[LAT_NAME].values.max()))
    
    lon_min = max(lon_vals.min() - lon_pad, float(lon_grid.min()))
    lon_max = min(lon_vals.max() + lon_pad, float(lon_grid.max()))
    
    def _lat_slice_local(coord, bounds):
        lower, upper = bounds
        if coord[0] > coord[-1]: lower, upper = upper, lower
        return slice(lower, upper)

    lat_slice = _lat_slice_local(ds[LAT_NAME].values, (lat_min, lat_max))
    
    if lon_min > lon_max:
        lon_slice = slice(None)
    else:
        lon_slice = slice(lon_min, lon_max)
        
    times = pd.to_datetime(track_df["time"])
    t_min = times.min() - pd.Timedelta(hours=6 * time_pad_steps)
    t_max = times.max() + pd.Timedelta(hours=6 * time_pad_steps)
    
    return ds.sel({LAT_NAME: lat_slice, LON_NAME: lon_slice, "time": slice(t_min, t_max)})

def persist_subset_to_netcdf(ds_subset: xr.Dataset, folder: Path, stem: str) -> Path:
    folder.mkdir(parents=True, exist_ok=True)
    nc_path = folder / f"{stem}.nc"
    
    ds_loaded = ds_subset.load()
    
    encoding = {}
    for name, da in ds_loaded.data_vars.items():
        if np.issubdtype(da.dtype, np.floating):
            encoding[name] = {"dtype": "float32", "zlib": False}
            
    ds_loaded.to_netcdf(nc_path, engine="netcdf4", encoding=encoding)
    return nc_path

def run_environment_extraction(
    ds_subset: xr.Dataset,
    track_df: pd.DataFrame,
    storm_id: str,
    output_root: Path,
    *,
    enable_detailed_shape_analysis: bool = False,
) -> dict:
    output_root.mkdir(parents=True, exist_ok=True)
    tracks_dir = output_root / "tracks_for_extractor"
    nc_dir = output_root / "nc_subsets"
    analysis_dir = output_root / "analysis_json"
    tracks_dir.mkdir(parents=True, exist_ok=True)
    analysis_dir.mkdir(parents=True, exist_ok=True)

    track_csv = tracks_dir / f"{storm_id}_track.csv"
    track_df.to_csv(track_csv, index=False)

    nc_path = persist_subset_to_netcdf(ds_subset, nc_dir, f"{storm_id}_subset")

    with TCEnvironmentalSystemsExtractor(
        str(nc_path),
        str(track_csv),
        enable_detailed_shape_analysis=enable_detailed_shape_analysis,
    ) as extractor:
        result = extractor.analyze_and_export_as_json(output_dir=str(analysis_dir))

    return {
        "json_dir": analysis_dir,
        "nc_path": nc_path,
        "track_csv": track_csv,
        "result": result,
    }

# ============================================================================
# 5. 多进程批处理配置
# ============================================================================

OUTPUT_ROOT = PROJECT_PATH / "colab_outputs"
TRACK_OUTPUT_DIR = OUTPUT_ROOT / "tracks"
INITIALS_CSV = TRACKS_CSV

# ⚡ 多进程配置
MAX_WORKERS = min(30, os.cpu_count() or 30)  # 并行进程数（32 核环境推荐 30）

print(f"🚀 批处理配置:")
print(f"   - 待处理风暴数: {len(valid_storm_ids)}")
print(f"   - 并行进程数: {MAX_WORKERS}")

# ============================================================================
# 6. 单个风暴处理函数 (适配多进程)
# ============================================================================

def process_single_storm_worker(args):
    """
    多进程 worker 函数
    注意：每个进程需要重新打开数据集连接
    """
    storm_id, dataset_url, tracks_csv_path, initials_csv_path, output_root_path, track_output_path = args
    
    import xarray as xr
    import pandas as pd
    import numpy as np
    import gc
    from pathlib import Path
    
    # 重新导入追踪和提取模块（每个进程独立）
    from initial_tracker.dataset_adapter import _DsAdapter, _build_batch_from_ds_fast
    from initial_tracker.initials import _load_all_points, _select_initials_for_time
    from initial_tracker.tracker import Tracker
    from initial_tracker.exceptions import NoEyeException
    from environment_extractor.extractor import TCEnvironmentalSystemsExtractor
    
    output_root = Path(output_root_path)
    track_output_dir = Path(track_output_path)
    
    try:
        # 1. 加载 tracks 数据
        df_tracks = pd.read_csv(tracks_csv_path)
        df_tracks["dt"] = pd.to_datetime(df_tracks["datetime"])
        
        storm_data = df_tracks[df_tracks["storm_id"] == storm_id]
        if storm_data.empty:
            return (storm_id, False, "Storm not found in tracks")
        
        storm_start_dt = storm_data["dt"].min()
        
        # 2. 计算空间范围
        pad_days, pad_deg = 1, 10.0
        start_dt = storm_data["dt"].min() - pd.Timedelta(days=pad_days)
        end_dt = storm_data["dt"].max() + pd.Timedelta(days=pad_days)
        
        lons = storm_data["longitude"].values
        lons_360 = np.where(lons < 0, lons + 360, lons)
        lon_min = max(0, lons_360.min() - pad_deg)
        lon_max = min(360, lons_360.max() + pad_deg)
        lat_min = max(-90, storm_data["latitude"].min() - pad_deg)
        lat_max = min(90, storm_data["latitude"].max() + pad_deg)
        
        # 3. 打开数据集（每个进程独立连接）
        ds_raw = xr.open_zarr(
            dataset_url,
            consolidated=True,
            storage_options={"token": "anon"},
        )
        
        rename_map = {
            "mean_sea_level_pressure": "msl",
            "10m_u_component_of_wind": "u10",
            "10m_v_component_of_wind": "v10",
            "u_component_of_wind": "u",
            "v_component_of_wind": "v",
            "temperature": "t",
            "specific_humidity": "q",
            "geopotential": "z",
            "land_sea_mask": "lsm",
            "2m_temperature": "t2m",
        }
        
        present = {src: dst for src, dst in rename_map.items() if src in ds_raw}
        ds_adapted = ds_raw[list(present.keys())].rename(present)
        
        if "z" in ds_adapted:
            ds_adapted["z"] = ds_adapted["z"] / 9.80665
            
        # Synthetic LSM
        if "lsm" not in ds_adapted:
            lat_dim = "latitude" if "latitude" in ds_adapted.coords else "lat"
            lon_dim = "longitude" if "longitude" in ds_adapted.coords else "lon"
            n_lat, n_lon = len(ds_adapted[lat_dim]), len(ds_adapted[lon_dim])
            ds_adapted["lsm"] = xr.DataArray(
                np.zeros((n_lat, n_lon), dtype=np.float32),
                coords={lat_dim: ds_adapted[lat_dim], lon_dim: ds_adapted[lon_dim]},
                dims=[lat_dim, lon_dim],
            )
        
        # 4. 切片获取风暴上下文
        LAT_NAME = "latitude" if "latitude" in ds_adapted.coords else "lat"
        LON_NAME = "longitude" if "longitude" in ds_adapted.coords else "lon"
        
        def _lat_slice(coord, bounds):
            lower, upper = bounds
            if coord[0] > coord[-1]: lower, upper = upper, lower
            return slice(lower, upper)
        
        lat_s = _lat_slice(ds_adapted[LAT_NAME].values, (lat_min, lat_max))
        lon_s = slice(lon_min, lon_max)
        
        ds_focus = ds_adapted.sel({
            LAT_NAME: lat_s,
            LON_NAME: lon_s,
            "time": slice(start_dt.strftime("%Y-%m-%d"), end_dt.strftime("%Y-%m-%d"))
        })
        
        if "time" not in ds_focus.dims and "time" not in ds_focus.coords:
            return (storm_id, False, "No time dimension")
        
        init_times = ds_focus["time"].values
        success_count = 0
        
        # 5. 遍历每个预报初始化时间
        for init_time in init_times:
            ts = pd.Timestamp(init_time)
            
            # 只处理 00Z 和 12Z 预报
            if ts.hour not in [0, 12]:
                continue
            
            init_str = ts.strftime("%Y%m%d_%H%M")
            
            try:
                # 准备单次预报数据集
                ds_single = ds_focus.sel(time=init_time)
                
                # 准备有效时间序列
                if "time" in ds_single.coords:
                    ds_run = ds_single.rename({"time": "init_time"})
                else:
                    ds_run = ds_single
                
                if "prediction_timedelta" in ds_run.coords:
                    pt = ds_run["prediction_timedelta"]
                    hours = (pt.values.astype("timedelta64[ns]").astype(float) / (3600 * 1e9))
                    keep_mask = (np.abs(hours % 6) < 0.01)
                    ds_run = ds_run.isel(prediction_timedelta=keep_mask)
                    
                    init_ts = pd.Timestamp(ds_run["init_time"].values)
                    lead_offsets = ds_run["prediction_timedelta"].values
                    if not np.issubdtype(lead_offsets.dtype, np.timedelta64):
                        lead_offsets = pd.to_timedelta(lead_offsets)
                    valid_times = init_ts + lead_offsets
                    
                    ds_run = ds_run.assign_coords(valid_time=("prediction_timedelta", valid_times))
                    ds_run = ds_run.swap_dims({"prediction_timedelta": "valid_time"})
                    ds_run = ds_run.rename({"valid_time": "time"})
                
                # 追踪开始时间
                tracking_start_time = max(ts, storm_start_dt)
                
                # 运行追踪
                adapter = _DsAdapter.build(ds_run)
                times_idx = pd.Index(adapter.times)
                
                if len(times_idx) == 0:
                    continue
                
                start_idx = int(np.argmin(np.abs(times_idx - tracking_start_time)))
                all_initials = _load_all_points(Path(initials_csv_path))
                init_candidates = _select_initials_for_time(all_initials, times_idx[start_idx], tol_hours=6)
                init_candidates = init_candidates[init_candidates["storm_id"] == storm_id]
                
                if init_candidates.empty:
                    continue
                
                row = init_candidates.iloc[0]
                init_lat = float(row["init_lat"])
                init_lon = float(row["init_lon"])
                if float(adapter.lons.min()) >= 0 and init_lon < 0:
                    init_lon = init_lon % 360
                
                init_wind = float(row["max_wind_usa"]) if pd.notna(row.get("max_wind_usa")) else None
                init_msl = float(row["min_pressure_usa"]) * 100.0 if pd.notna(row.get("min_pressure_usa")) else None
                
                tracker = Tracker(
                    init_lat=init_lat,
                    init_lon=init_lon,
                    init_time=times_idx[start_idx],
                    init_msl=init_msl,
                    init_wind=init_wind,
                )
                
                last_idx = min(len(adapter.times), start_idx + 40)
                for time_idx in range(start_idx, last_idx):
                    batch = _build_batch_from_ds_fast(adapter, time_idx)
                    try:
                        tracker.step(batch)
                    except NoEyeException:
                        if time_idx == start_idx:
                            tracker = None
                            break
                        continue
                    if tracker.dissipated:
                        break
                
                if tracker is None:
                    continue
                
                track_df = tracker.results()
                track_df["storm_id"] = storm_id
                track_df["particle"] = storm_id
                
                forecast_unique_id = f"{storm_id}_{init_str}"
                
                # 保存追踪结果
                track_output_dir.mkdir(parents=True, exist_ok=True)
                track_save_path = track_output_dir / f"track_{forecast_unique_id}.csv"
                track_df.to_csv(track_save_path, index=False)
                
                # 环境场提取
                lat_vals = track_df["lat"].astype(float)
                lon_vals = track_df["lon"].astype(float)
                lon_grid = ds_run[LON_NAME].values
                if float(lon_grid.min()) >= 0:
                    lon_vals = lon_vals % 360
                
                lat_min_t = max(lat_vals.min() - 8.0, float(ds_run[LAT_NAME].values.min()))
                lat_max_t = min(lat_vals.max() + 8.0, float(ds_run[LAT_NAME].values.max()))
                lon_min_t = max(lon_vals.min() - 8.0, float(lon_grid.min()))
                lon_max_t = min(lon_vals.max() + 8.0, float(lon_grid.max()))
                
                lat_s_t = _lat_slice(ds_run[LAT_NAME].values, (lat_min_t, lat_max_t))
                lon_s_t = slice(lon_min_t, lon_max_t)
                
                times_track = pd.to_datetime(track_df["time"])
                t_min = times_track.min() - pd.Timedelta(hours=6)
                t_max = times_track.max() + pd.Timedelta(hours=6)
                
                local_ds = ds_run.sel({LAT_NAME: lat_s_t, LON_NAME: lon_s_t, "time": slice(t_min, t_max)})
                
                # 保存并提取
                tracks_dir = output_root / "tracks_for_extractor"
                nc_dir = output_root / "nc_subsets"
                analysis_dir = output_root / "analysis_json"
                tracks_dir.mkdir(parents=True, exist_ok=True)
                nc_dir.mkdir(parents=True, exist_ok=True)
                analysis_dir.mkdir(parents=True, exist_ok=True)
                
                track_csv = tracks_dir / f"{forecast_unique_id}_track.csv"
                track_df.to_csv(track_csv, index=False)
                
                nc_path = nc_dir / f"{forecast_unique_id}_subset.nc"
                ds_loaded = local_ds.load()
                encoding = {}
                for name, da in ds_loaded.data_vars.items():
                    if np.issubdtype(da.dtype, np.floating):
                        encoding[name] = {"dtype": "float32", "zlib": False}
                ds_loaded.to_netcdf(nc_path, engine="netcdf4", encoding=encoding)
                
                with TCEnvironmentalSystemsExtractor(
                    str(nc_path),
                    str(track_csv),
                    enable_detailed_shape_analysis=False,
                ) as extractor:
                    extractor.analyze_and_export_as_json(output_dir=str(analysis_dir))
                
                success_count += 1
                
                # 清理
                del local_ds, ds_loaded
                gc.collect()
                
            except Exception as e:
                continue
            
            del ds_run
            gc.collect()
        
        ds_focus.close()
        ds_raw.close()
        del ds_focus, ds_raw, ds_adapted
        gc.collect()
        
        if success_count > 0:
            return (storm_id, True, f"Processed {success_count} forecasts")
        else:
            return (storm_id, False, "No forecasts processed")
        
    except Exception as e:
        import traceback
        return (storm_id, False, f"Error: {str(e)}\n{traceback.format_exc()}")

# ============================================================================
# 7. Google Drive 同步 (已取消)
# ============================================================================

# 已取消后台同步；输出直接写入 OUTPUT_ROOT。

# ============================================================================
# 8. 执行多进程批处理
# ============================================================================

print(f"\n{'='*60}")
print(f"🚀 开始多进程批处理")
print(f"{'='*60}")

# 准备多进程参数
worker_args = [
    (
        storm_id,
        DATASET_URL,
        str(TRACKS_CSV),
        str(INITIALS_CSV),
        str(OUTPUT_ROOT),
        str(TRACK_OUTPUT_DIR),
    )
    for storm_id in valid_storm_ids
]

successful_storms = []
failed_storms = []
start_time = time.time()

# 使用多进程池
print(f"⏳ 使用 {MAX_WORKERS} 个进程并行处理 {len(worker_args)} 个风暴...")

try:
    with Pool(processes=MAX_WORKERS) as pool:
        # 使用 imap_unordered 获取实时结果
        for i, result in enumerate(pool.imap_unordered(process_single_storm_worker, worker_args)):
            storm_id, success, message = result
            
            if success:
                successful_storms.append(storm_id)
                print(f"✅ [{i+1}/{len(worker_args)}] {storm_id}: {message}")
            else:
                failed_storms.append((storm_id, message))
                print(f"❌ [{i+1}/{len(worker_args)}] {storm_id}: {message[:100]}...")
            
            # 每处理 10 个风暴打印一次进度
            if (i + 1) % 10 == 0:
                elapsed = time.time() - start_time
                rate = (i + 1) / elapsed * 3600
                print(f"📊 进度: {i+1}/{len(worker_args)} ({(i+1)/len(worker_args)*100:.1f}%) | 速率: {rate:.1f} storms/hour")

except KeyboardInterrupt:
    print("\n⚠️ 用户中断处理")
finally:
    pass

# 最终统计
elapsed_total = time.time() - start_time
print(f"\n{'='*60}")
print(f"🎉 批处理完成!")
print(f"{'='*60}")
print(f"✅ 成功: {len(successful_storms)}")
print(f"❌ 失败: {len(failed_storms)}")
print(f"⏱️ 总耗时: {elapsed_total/3600:.2f} 小时")
print(f"📈 平均速率: {len(worker_args)/elapsed_total*3600:.1f} storms/hour")

print(f"📍 输出目录: {OUTPUT_ROOT}")

🚀 Starting Batch Processing for 256 storms...
Using ThreadPoolExecutor with 1 workers.

Processing Storm: 2016007N27285
   [2016007N27285] 📅 Start Time: 2016-01-07 00:00


[2016007N27285] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2016007N27285_colab.csv
   [2016007N27285] ✅ Track generated: 43 steps
   [2016007N27285] 🌪️ Extracting environment...
📊 加载43个热带气旋路径点
🌍 区域范围: 16.5°-67.0°N, 276.8°-341.0°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016007N27285] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json
📊 加载43个热带气旋路径点
🌍 区域范围: 16.5°-67.0°N, 276.8°-341.0°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016007N27285] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json

Processing Storm: 2016040S16155
   [2016040S16155] 📅 Start Time: 2016-02-09 00:00

Processing Storm: 2016040S16155
   [2016040S16155] 📅 Start Time: 2016-02-09 00

[2016040S16155] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2016040S16155_colab.csv
   [2016040S16155] ✅ Track generated: 31 steps
   [2016040S16155] 🌪️ Extracting environment...
📊 加载31个热带气旋路径点
🌍 区域范围: -33.8°--7.5°N, 145.5°-168.8°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016040S16155] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json
📊 加载31个热带气旋路径点
🌍 区域范围: -33.8°--7.5°N, 145.5°-168.8°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016040S16155] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json

Processing Storm: 2016148N27288
   [2016148N27288] 📅 Start Time: 2016-05-27 06:00

Processing Storm: 2016148N27288
   [2016148N27288] 📅 Start Time: 2016-05-27 

[2016148N27288] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2016148N27288_colab.csv
   [2016148N27288] ✅ Track generated: 56 steps
   [2016148N27288] 🌪️ Extracting environment...
📊 加载56个热带气旋路径点
🌍 区域范围: 19.2°-44.0°N, 271.8°-339.8°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016148N27288] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json
📊 加载56个热带气旋路径点
🌍 区域范围: 19.2°-44.0°N, 271.8°-339.8°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016148N27288] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json

Processing Storm: 2016158N22272
   [2016158N22272] 📅 Start Time: 2016-06-05 12:00

Processing Storm: 2016158N22272
   [2016158N22272] 📅 Start Time: 2016-06-05 12

[2016171N19268] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2016171N19268_colab.csv
   [2016171N19268] ✅ Track generated: 9 steps
   [2016171N19268] 🌪️ Extracting environment...
📊 加载9个热带气旋路径点
🌍 区域范围: 9.5°-27.2°N, 260.5°-278.2°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016171N19268] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json
📊 加载9个热带气旋路径点
🌍 区域范围: 9.5°-27.2°N, 260.5°-278.2°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...
⏩ 检测到当前NC对应的所有分析结果已存在于 '/content/TianGong-AI-Cyclone/colab_outputs/analysis_json' (共1个)，跳过重算。
   [2016171N19268] ✅ Extraction complete. Results in /content/TianGong-AI-Cyclone/colab_outputs/analysis_json

Processing Storm: 2016183N13246
   [2016183N13246] 📅 Start Time: 2016-07-01 06:00

Processing Storm: 2016183N13246
   [2016183N13246] 📅 Start Time: 2016-07-01 06:00
[

...

Traceback (most recent call last):
  File "/tmp/ipython-input-1900234399.py", line 130, in process_single_storm
    tracking_results = track_cyclones_from_dataset(
                       ^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/tmp/ipython-input-3159545257.py", line 89, in track_cyclones_from_dataset
    tracker.step(batch)
  File "/content/TianGong-AI-Cyclone/src/initial_tracker/tracker.py", line 149, in step
    if is_clear(lat, lon, delta):
       ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/content/TianGong-AI-Cyclone/src/initial_tracker/tracker.py", line 144, in is_clear
    return lsm_box.max() < 0.5
           ^^^^^^^^^^^^^
  File "/usr/local/lib/python3.12/dist-packages/numpy/_core/_methods.py", line 44, in _amax
    return umr_maximum(a, axis, None, out, keepdims, initial, where)
           ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
ValueError: zero-size array to reduction operation maximum which has no identity


[2017300N10271] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2017300N10271_colab.csv
   [2017300N10271] ✅ Track generated: 11 steps
   [2017300N10271] 🌪️ Extracting environment...
📊 加载11个热带气旋路径点
🌍 区域范围: 2.5°-21.5°N, 261.5°-280.0°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...

🌀 正在处理台风事件: 2017300N10271
  -> 分析时间点: 2017-10-26 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_component_labeling
⚠️  使用t2m作为海表温度近似
✅ 方法1成功: 连通区域标注提取到248个点
🔒 边界闭合: 添加首点，闭合距离从6.01°降至0
  -> 分析时间点: 2017-10-26 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_component_labeling
⚠️  使用t2m作为海表温度近似
✅ 方法1成功: 连通区域标注提取到249个点
🔒 边界闭合: 添加首点，闭合距离从6.01°降至0
📊 加载11个热带气旋路径点
🌍 区域范围: 2.5°-21.5°N, 261.5°-280.0°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...

🌀 正在处理台风事件: 2017300N10271
  -> 分析时间点: 2017-10-26 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_component_labeling
⚠️  使用t2m作为海表温度近似
✅ 方法1成功: 连通区域标注提取到248个点
🔒 边界闭合: 添加首点，闭合距离从6.01°降至0
  -> 分析时间点: 2017-10-26 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_compon

[2017301N18276] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2017301N18276_colab.csv
   [2017301N18276] ✅ Track generated: 11 steps
   [2017301N18276] 🌪️ Extracting environment...
📊 加载11个热带气旋路径点
🌍 区域范围: 9.5°-32.5°N, 267.0°-288.8°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...

🌀 正在处理台风事件: 2017301N18276
  -> 分析时间点: 2017-10-27 18:00
📊 加载11个热带气旋路径点
🌍 区域范围: 9.5°-32.5°N, 267.0°-288.8°E
⚡ 形状分析快速模式已启用（跳过昂贵计算，性能提升 60-80%）

🔍 开始进行专家级环境场解译并构建JSON...

🌀 正在处理台风事件: 2017301N18276
  -> 分析时间点: 2017-10-27 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_component_labeling
⚠️  使用t2m作为海表温度近似
✅ 方法1成功: 连通区域标注提取到122个点
🔒 边界闭合: 添加首点，闭合距离从11.10°降至0
  -> 分析时间点: 2017-10-27 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_component_labeling
⚠️  使用t2m作为海表温度近似
✅ 方法1成功: 连通区域标注提取到122个点
🔒 边界闭合: 添加首点，闭合距离从11.10°降至0
  -> 分析时间点: 2017-10-27 18:00
✅ 边界提取成功: 51点, 闭合, 方法: connected_component_labeling
⚠️  使用t2m作为海表温度近似
✅ 方法1成功: 连通区域标注提取到140个点
🔒 边界闭合: 添加首点，闭合距离从1.27°降至0
  -> 分析时间点: 2017-10-28 00:00
✅ 边界提取成功

[2017309N26308] track saved to /content/TianGong-AI-Cyclone/colab_outputs/tracks/track_2017309N26308_colab.csv
   [2017309N26308] ✅ Track generated: 27 steps
   [2017309N26308] 🌪️ Extracting environment...


: 

## Environment Extraction Helpers

To reuse `TCEnvironmentalSystemsExtractor`, we slice a compact cube around each track, dump it to NetCDF (typically <1 GB), and feed the existing extractor class.

In [ ]:
### (Merged) Environment Extraction Helpers

*The helper functions `subset_dataset_for_track` and `run_environment_extraction` have been moved to the main execution cell above to support batch processing.*


### Run Environment Extraction

Pick one of the generated tracks, carve out a compact cube around it, persist the subset, and invoke the extractor. Disable `enable_detailed_shape_analysis` to save roughly 60% runtime in Colab.

In [ ]:
### (Merged) Run Environment Extraction

*The execution logic has been integrated into the batch processing loop above.*


## 操作说明与后续步骤

### 🖥️ HPC 云服务器说明

本版本不再包含 Google Drive/rclone 同步步骤。

### ☁️ 数据输出与持久化

已取消 Google Drive/rclone 同步：所有输出直接写入项目目录内的 `colab_outputs/`。

---

### ⚙️ 多进程配置调整

在批处理 cell 中可以调整以下参数：
- `MAX_WORKERS = 30` - 并行进程数（32 核环境推荐 30）

---

### 📊 输出目录结构

```
colab_outputs/
├── tracks/                    # 追踪结果 CSV
├── tracks_for_extractor/      # 环境提取用的追踪文件
├── nc_subsets/                # NetCDF 子集文件
└── analysis_json/             # 环境场分析 JSON 结果
```

---

### 🔧 性能优化建议

- HPC 上建议使用 `MAX_WORKERS` = CPU 核心数 - 2
- 内存密集型任务可降低 `MAX_WORKERS` 至 8-10
- 如遇 OOM 错误，减少并行数或增加 `gc.collect()` 频率

---

### 📋 完整工作流程

1. **运行 Cell 1-6**: 检查环境、确认在仓库目录
2. **运行 Cell 8**: 环境检测和路径配置  
3. **运行 Cell 12**: 安装依赖
4. **运行 Cell 14**: 验证模块导入
5. **运行 Cell 15**: 验证数据集可访问性
6. **运行 Cell 17**: 加载 tracks 数据
7. **运行 Cell 19**: 定义追踪辅助函数
8. **运行 Cell 21**: 🚀 开始多进程批处理
9. **运行 Cell 28**: 检查结果

## 结果检查

In [ ]:
# ============================================================================
# 结果检查（输出已直接写入项目目录）
# ============================================================================

# 检查输出目录状态
from pathlib import Path
import os

output_dirs = {
    "tracks": OUTPUT_ROOT / "tracks",
    "tracks_for_extractor": OUTPUT_ROOT / "tracks_for_extractor", 
    "nc_subsets": OUTPUT_ROOT / "nc_subsets",
    "analysis_json": OUTPUT_ROOT / "analysis_json",
}

print("📁 输出目录统计:")
print("="*50)
total_size = 0
for name, path in output_dirs.items():
    if path.exists():
        files = list(path.glob("*"))
        size = sum(f.stat().st_size for f in files if f.is_file()) / (1024**2)
        total_size += size
        print(f"  {name}: {len(files)} 文件, {size:.2f} MB")
    else:
        print(f"  {name}: 目录不存在")
print(f"\n  总计: {total_size:.2f} MB")
print("="*50)

print(f"\n📍 输出目录: {OUTPUT_ROOT}")